# CS 584 Project Topic 2 -- Toxic Spans Detection 

#### Name: Harsh RM
#### Stevens ID: 20005252

In [1]:
!pip install -r requirements.txt

  Using cached typing_extensions-3.7.4.3-py3-none-any.whl (22 kB)


  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.4.0
    Uninstalling typing_extensions-4.4.0:
      Successfully uninstalled typing_extensions-4.4.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
pydantic 1.10.2 requires typing-extensions>=4.1.0, but you have typing-extensions 3.7.4.3 which is incompatible.
bokeh 2.4.2 requires typing-extensions>=3.10.0, but you have typing-extensions 3.7.4.3 which is incompatible.


In [2]:
!pip install stanza
!pip install transformers

## 1. Importing Libraries

In [3]:
import numpy as np
import pandas as pd
import tensorflow as tf
import gc
import json
import stanza
from tensorflow.keras import *
import tensorflow as tf
import tensorflow as tf
import tensorflow_addons as tfa
from keras import backend
from typing import List, Tuple, Union
from sklearn.model_selection import KFold
from sklearn.metrics import classification_report
from transformers import TFRobertaModel,RobertaTokenizer
from tensorflow.keras.layers import Layer, InputSpec


tf.config.list_physical_devices('GPU')

2022-12-21 15:45:35.338085: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-12-21 15:45:35.338107: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
/home/harsh/anaconda3/lib/python3.9/site-packages/tensorflow_addons/utils/ensure_tf_install.py:53: UserWarning: Tensorflow Addons supports using Python ops for all Tensorflow versions above or equal to 2.6.0 and strictly below 2.9.0 (nightly versions are not supported). 
 The versions of TensorFlow you are currently using is 2.5.3 and is not supported. 
Some things might work, some things might not.
If you were to encounter a bug, do not file an issue.
If you want to make sure you're using a tested and supported configuration, either change the TensorFlow version or the TensorFlow Addons's version. 
You c

[]

In [4]:
!pip install tensorflow-addons==0.16.1

## 2. Data Processing

* Download the dataset
* Load data to text and labels
* Preprocessing
* Tokenization
* Split data

In [5]:
import os
import nltk

nltk_path = os.path.join('Project_data', 'nltk')
nltk.download('stopwords', download_dir = nltk_path)
nltk.data.path.append(nltk_path)

[nltk_data] Downloading package stopwords to Project_data/nltk...
[nltk_data]   Unzipping corpora/stopwords.zip.


In [6]:
import sys


def print_line(*args):
    """ Inline print and go to the begining of line
    """
    args1 = [str(arg) for arg in args]
    str_ = ' '.join(args1)
    sys.stdout.write(str_ + '\r')
    sys.stdout.flush()

### 1.1 Load data

- Load sentences and labels
- Transform string labels into integers

In [7]:
def load_sentence_label(data_path: str) -> Tuple[List[str], List[str]]:
    """ Load sentences and labels from the specified path
    Args:
        data_path: data_path: path to the data file, e.g., 'a1-data/SMSSpamCollection'
        sentences: the raw text list of all sentences
    Returns:
        labels: the label list of all sentences
    """
    sentences, labels = [], []
    # Start your code here (load text and label from files)
    dataframe = open(data_path, mode = 'r')
    for i in dataframe.read().splitlines():
        line = i.split("\t")
        sentences.append(line[1])
        labels.append(line[0])
    # End
    return sentences, labels

In [8]:
# data_path = os.path.join('Project_data', 'tsd_train.csv')
# sentences, labels = load_sentence_label(data_path)

# label_map = {}
# for label in sorted(list(set(labels))):
#     label_map[label] = len(label_map)
# labels = np.array([label_map[label] for label in labels], dtype = int)
# sentences = np.array(sentences, dtype = object)

# print('Label map:', label_map)
# print('Number of sentences and labels:', len(sentences), len(labels))

In [9]:
dataframe = pd.read_csv("/home/harsh/Documents/Academics/CS 584 - NLP/Final_project/data/tsd_train.csv")

In [10]:
print(dataframe)

                                                  spans  \
0     [8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19,...   
1                          [33, 34, 35, 36, 37, 38, 39]   
2                                          [0, 1, 2, 3]   
3             [7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17]   
4                          [32, 33, 34, 35, 36, 37, 38]   
...                                                 ...   
7934                                     [8, 9, 10, 11]   
7935  [48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 5...   
7936  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13,...   
7937                            [5, 6, 7, 8, 9, 10, 11]   
7938  [106, 107, 108, 109, 110, 169, 170, 171, 172, ...   

                                                   text  
0     Another violent and aggressive immigrant killi...  
1     I am 56 years old, I am not your fucking junio...  
2                     Damn, a whole family. Sad indeed.  
3     What a knucklehead. How can anyone not know th...  
4

In [11]:
type(dataframe)

pandas.core.frame.DataFrame

In [12]:
df = dataframe.values.tolist()

In [13]:
df[7938]

['[106, 107, 108, 109, 110, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182]',
 'Who is this "we" of which you speak? Are you really a woman, Lars? If not then concern yourself with your penis and other genital and reproductive parts and stay out of women\'s bodies.']

In [14]:
df[0]

['[8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39]',
 'Another violent and aggressive immigrant killing a innocent and intelligent US Citizen.... Sarcasm']

In [15]:
type(df[0][0])

str

In [16]:
res = json.loads(df[0][0])
print(res)

[8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39]


In [17]:
df[0][0]

'[8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39]'

In [18]:
len(df)

7939

In [19]:
res = []
for i in range(len(df)):
    df[i][0] = json.loads(df[i][0])

In [20]:
for i in range(len(df)):
    print(df[i])

[[8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39], 'Another violent and aggressive immigrant killing a innocent and intelligent US Citizen.... Sarcasm']
[[33, 34, 35, 36, 37, 38, 39], 'I am 56 years old, I am not your fucking junior pal. What you are saying makes no sense. I don\'t know what you are basing this on. The cheap black market crap is still coming up from Mexican nationals, and the good stuff from BC and Humbolt.  The I5 corridor is still just as busy, and they are still making a ton of money. Nothing has really changed except that the legal market has made it easy for anyone of legal age to buy it.  And the legal market is controlled by corporate growers with million dollar facilities, or a co-op of smaller growers. The Federal government "war on drugs" really has no impact on the legal market in Oregon. I don\'t see any glutton of weed, whatever that means.']
[[0, 1, 2, 3], 'Damn, a whole family.

[[171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189], "Tiger doesn't change his strips, plus, his followers all point to his multiple bankruptcies and thousands of lawsuits as some great 'business record' to be proud of ... \n\nStupid is as stupid does, Gump was right.\n\nRepublicans need to be shot into the sun."]
[[], "No, I graduated with a dual masters in history and political science many years ago. I know poppycock when I see it!! And you are all bull poo. Today's democrats and their voters are socialist. Read history and political platforms. Nazis are socialist. So are communist, the Nazis were right of communism. Therefore the liberals of America took advantage of the term right wing of the right socialist in Germany. If you disagree your either intellectually dishonest or stupid. Pick your poison."]
[[308, 309, 310, 311, 312, 313, 314, 315, 316, 317, 318, 319, 320], 'It\'s too bad Walker won\'t curb his spending of billions on the "s

[[552, 553, 554, 555, 556, 557, 558, 559, 560, 561, 562, 563, 564, 565, 566, 567, 568, 569, 570, 571], '"Mr. Pinsonneault( National Bank) said the ratio has now climbed back to its long-term average level of 2.5 per cent.....which suggests the market is in balance in the region, limiting the risk of a significant further price correction."\n____\nAre you fore real? What you are saying makes absolutely no sense! Find some other stat to warp to try and pump up the RE market. I guess your flawed Tetranet-NB Index is not enough!\n\nPretty sure you did this interview by the phone, it would be impossible not to turn red or laugh out loud as you present your ridiculous "analysis".']
[[78, 79, 80, 81, 82, 83], 'Free heels, you forgot the Trump Bunny motto : "Vote For Trump. You Can\'t Fix Stupid. "']
[[73, 74, 75, 76, 77, 78], 'Margaret Conaway, thank you for your excellent letter!  And yes Kelly is insane.']
[[7, 8, 9, 10, 11, 12, 13, 14, 15, 16], "You're ridiculous, hateful, spiteful person 

[[155, 156, 157, 158, 159, 160, 213, 214, 215, 216, 217, 218, 219, 220, 221], 'This debacle the city created is the problem of the city. The state is not responsible to fix it. Caldwell needs to wake up & accept that this project was doomed from the start. Donʻt blame the state for your own stupidity. Its like financing a house for $1 million them blaming your neighbor when you canʻt afford to pay for it.']
[[36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53], "Another reason he can't here is his brains are damaged."]
[[280, 281, 282, 283], 'I can imagine you right now in a corner of your house rocking back and forth, clutching your pearls, holding yourself and chanting, "racists, bigots, flame throwers, sexists..." Anyone who doesn\'t love the homeless and want to cuddle them like human teddy bears is obviously just scum!']
[[253, 254, 255, 256, 257, 258, 259, 260, 261, 262, 263, 264, 265, 266, 267, 268, 269, 270], 'Why thank you for your vey civil remark.  I agre

[[258, 259, 260, 261, 262], 'Thanks Blankenyblank. These threads say it all. True "nimrods" don\'t need or want a lazy way to show there marksmanship abilities. Personally, I\'ve always respected the bow & arrow hunter much more. The skill it requires takes years of practice. tRump is an idiot suggesting that Clinton wants to take away people\'s right to bear arms, not WMDs. Only the uneducated tRump supporter thinks otherwise.']
[[21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 343, 344, 345, 346, 347], 'I would not consider these troublemakers "liberals" in any fashion; the actual liberals stayed at the peaceful protest.  For years Eugene\'s liberals have been plagued by these anarchists and other extremists who give liberals and Progressives  a bad name, and now that our nation faces a crisis of authoritarianism we need to make clear these fools do NOT speak for us.']
[[115, 116, 117, 118, 119, 120, 121, 122, 123, 1

...

[[18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35], 'LAUGHED OUT LOUD.\nPathetic President.\nITMFA\nITMFA\nITMFA\nITMFA\nITMFA!']
[[83, 84, 85, 86, 87, 88], "What an absurd little man.  Shows that the US doesn't have a monopoly on political idiots."]
[[367, 368, 369, 370], "[I am highly suspect of anyone that publicly supports the taxi system that we currently have in Anchorage...Either you don't get out much or you own a taxi medallion.]\nBecause anyone who criticizes Uber/Lyft or even the law that benefits them must (by foolish guilt by association) be supporting the taxi system?  A person cannot possible support Uber/Lyft and still have a problem with the passage of this bill?  That the problem isn't the status quo but about how hypocrites in the Legislature constantly criticize the federal government and then do the exact same thing?"]
[[133, 134, 135, 136, 137], 'Then schools should not try to fund, through alternative sources, any mandate by the federal gov

[[15, 16, 17, 18, 19, 20, 21, 22], 'Ethics are for schmucks. This lesson is being taught from the very top in D.C., on down to the current part-time HNL mayor...']
[[47, 48, 49, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148], "But aren't you all getting really tired of the gay in your face propaganda day after day. Why can't they simply go to a different gay friendly bakery?  Instead they continue to try and force their lifestyle down all of our throats and destroy good people in the process. I for one am sick of it all. Time for a straight pride parade!"]
[[117, 118, 119, 120, 121, 122, 123, 124, 125], "Trump's total ignorance is alarming and puts America's security at risk.  He is a joke but now that he has power his stupidity is a danger to us."]
[[

[[321, 322, 323, 324], 'Looking at the amout of money ANTHC and SCF love to piss away and the fondness that their "Customer Owners" have for the park, why don\'t they freshen that place up? Oh wait that\'s mostly tax money too. Whoops.... ha, So the trees are getting wasted and pissing everywhere so we have to cut them down... summed up best... dumb']
[[67, 68, 69, 70, 71], "“When I was a young man a clever old man said to me Jacob you'r an IDIOT"]
[[125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 157, 158, 159, 160, 161], "Just think how much smarter and better looking than you she is. That's the true reason you feminazis hate her. You are all a bunch of nasty hags,, angry and weird."]
[[346, 347, 348, 349, 350, 351, 352, 353], 'You mean the problem in 2016 is that most of what she says (and for the last 30 years for that matter) is a lie.  Yes, this country is in crisis, the government is a disaster  (may I say corruption), and the laws 

[[198, 199, 200, 201, 202, 203], 'I too applaud the Officer who confronted someone with a "toy" gun. And of course I wonder what could possibly have motivated the guy to this level of provocation. Was he suicidal or just incredibly stupid?']
[[159, 160, 161, 162, 168, 169, 170, 171, 172, 173, 174, 175, 176], 'So a majority of Alaska taxpayers voted for Trump over the terrible Hillary, and this is supposed to make them feel "comfortable" ???  The UAA is just a total liar and hypocrite.']
[[62, 63, 64, 65], 'I never understood the need for men to take pictures of their junk and then share them.']
[[81, 82, 83, 84, 85], 'Please fill us in on the verifiable events that would qualify the President as a moron.']
[[26, 27, 28, 29], "Cool, let's go shoot more sh*t!!!"]
[[11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 46, 47, 48, 49, 50], 'An elected fool is still a fool. Not sure why folks think they will suddenly become capable in office.']
[[99, 100, 101, 102

[[5, 6, 7, 8], 'this crap never ends']
[[220, 221, 222, 223, 224, 225, 226, 227, 228, 229, 230, 231], 'well sad as it may seem noone was left to die in a ditch and nlone was gone from the scene of the wreck atleaset this indvidual wasnt able to drive away go home leave a note for mommy and daddy that i was in somecrash i killed a man goodnight']
[[64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74], '"a plan to steal the 63-year-old’s trailer home"\n.\nThe ultimate white-trash heist!']
[[0, 1, 2, 3, 4, 5, 6, 7, 8], "Hypocrite, much? Just like the weasel you voted for, I see. He lied about how he'd return power to the people and you fell for it. \nTrump Bunnies are easily conned."]
[[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81

In [21]:
df[0][0][len(df[0][0])-1]

39

In [22]:
first = df[2][0][0]
last = df[2][0][-1]
print(first)
print(last)

0
3


In [23]:
res = df[2][1][first:last+1]
print(res)

Damn


In [24]:
print(type(res))

<class 'str'>


In [25]:
sentences = []
count = 0
for i in range(len(df)):
    if len(df[i][0]) == 0:
        count += 1
print(count)
for i in range(len(df)):
    if len(df[i][0]) != 0:
        first = df[i][0][0]
        last = df[i][0][-1]
        sentences += [df[i][1][first:last+1]]

485


In [26]:
print(sentences)

['violent and aggressive immigrant', 'fucking', 'Damn', 'knucklehead', 'killing', 'stupid emoticons', 'Dumb', "idiots who don't want something else passed that's going to save your free healthcare are kind of stupid", 'pathetic', 'imbecile', 'idiot', 'repugnant', 'joke', 'protest', 'f*** you', 'stupid', 'sociopathic and parasitic', "sycophants think he's being tough, when in fact, Trump is being an imbecile.  LeBron James is right.  Trump is a bum", 'dumb', 'Kill some more kids and then complain about guns, LOL the left is a joke', 'fool', 'ignorant', 'Damn', 'stupid', 'mistake', 'scam', 'ignorant propaganda believing alt left sheep,, no loser trump is making great progress regardless of the lunatic opposition fromtthe dems.. .. no one is saying  attack iran but as usual you lunatics', 'violent and extremist doctrines as Islamists are', 'ignorant', 'testicles.\n\nIt is really quite stupid', "I'll shoot you if I catch you in my vehicles stealing then call the police.\nDon't worry you wo

In [27]:
len(sentences)

7454

In [28]:
for i in range(len(df)):
    print(df[i])

[[8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39], 'Another violent and aggressive immigrant killing a innocent and intelligent US Citizen.... Sarcasm']
[[33, 34, 35, 36, 37, 38, 39], 'I am 56 years old, I am not your fucking junior pal. What you are saying makes no sense. I don\'t know what you are basing this on. The cheap black market crap is still coming up from Mexican nationals, and the good stuff from BC and Humbolt.  The I5 corridor is still just as busy, and they are still making a ton of money. Nothing has really changed except that the legal market has made it easy for anyone of legal age to buy it.  And the legal market is controlled by corporate growers with million dollar facilities, or a co-op of smaller growers. The Federal government "war on drugs" really has no impact on the legal market in Oregon. I don\'t see any glutton of weed, whatever that means.']
[[0, 1, 2, 3], 'Damn, a whole family.

[[123, 124, 125, 126, 127, 138, 139, 140, 141, 142, 143, 171, 172, 173, 174, 175, 176, 177], "Rally 'round the insane cheeto boy's, the nut job wants to start Armageddon. The only people who will rally around this a**clown, are the idiots who voted for this insane jacka**. They can't be wrapped real tight either."]
[[143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160], 'Hey ms.amylou, you are rude, you call names, you are mean spirited much of the time, as are most Trump supporters.  I haven\'t seen you telling your nasty buddies to stop their nasty little jabs.  You can start with Nick Travis and waveamaker. 99.9%of the comments I review on here are "mean spirited" remarks by Trump supporters so don\'t presume to lecture me.  Got it?']
[[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55,

[[39, 40, 41, 42, 43, 44], 'Ha! I disagree with Schumer and Pelosi almost 100% of the time - but my bet would be on them snookering the idiot Trump.']
[[63, 64, 65, 66, 67, 68, 69], 'The biggest enemy of science is todays sciencetists....and the moronic media that follows them.']
[[47, 48, 49, 50, 51, 52], 'I cannot tell if you are trolling or just that stupid???']
[[0, 1, 2, 3, 4, 5, 6, 7], 'Dumb ass']
[[15, 16, 17, 18, 19, 20, 21, 22, 51, 52, 53, 54, 55, 56, 57], 'So, if this is accurate, which I doubt, extremists Muslims attack and kill Britons in Britain and there is a backlash against extremist Muslims by Britons in Britain.  Go figure.']
[[34, 35, 36, 37, 38, 65, 66, 67, 68, 69], 'Our loss, their gain.  Just a few fools ruining it just like The Ferry to the outer islands.']
[[70, 71, 72, 73, 74, 75, 76], 'Actually, the Ukrainian military is doing quite well when it comes to killing off the Russian invaders. More power to them.']
[[218, 219, 220, 221, 222, 223, 224], "So if Trump 

[[58, 59, 60, 61, 62, 63], 'Again...\n"trump wants war with millions dead" = You are a sadist \n"he is a huge danger to america" = You see his agenda working and are scared!']
[[51, 52, 53, 54], 'I guess Judge Watson finally realized that Chin is nuts.']
[[0, 1, 2, 3, 4, 5], 'Stupid headline! He is not whining or blaming anyone. He is stating a fact. Election fraud is widespread. - Georgana Davis']
[[13, 14, 15, 16, 17], 'Or the other idiot to suggest a used Toureg TDI.']
[[11, 12, 13, 14, 15, 16], 'mr kamkar, stupid may be legal but it is still enough to put you out of your job.   great leadership there sir.']
[[107, 108, 109, 110, 111, 194, 195, 196, 197, 198, 199, 200, 201, 202], "Mr Elway, The Denver Broncos are NOT as big or as great as the United States of America, and telling these fools 'it's okay with the bronco's to disparage our anthem and flag'  is wrong!  Get a grip dope."]
[[293, 294, 295, 296, 297, 298, 299, 300, 301, 302, 303, 304], '"The photo of U.S. President Donald 

[[10, 11, 12, 13, 14], 'You are a swine.']
[[150, 151, 152, 153], 'The 3 county commissioners NEED TO STICK TO COUNTY ISSUES!\nAND STAY THE HELL OUT OF SCHOOL/OMC ISSUES!!!!!!!!!!!!!!!!!!!!!!!!!!!\nI am so sick of this crap!\nAlso its damn time to GET rid of all of the OMC commissioners and the CEO that is very much overpaid!!!!!!!!!!!!!!!!!!!!!!!!']
[[81, 82, 83, 84, 85, 86, 295, 296, 297, 298, 299, 300, 301, 302, 303, 304, 305, 306, 307, 308], 'The author quite rightly states that the Finsbury Park crime did not happen in a vacuum.  She then goes on to completely ignore the crimes committed by Muslims.  While I am not excusing the various attacks against Muslims, which are unforgivable, one cannot ignore the mass murders committed by Muslims either.']
[[19, 20, 21, 22, 23, 24, 25, 26, 27], 'Any way we can ban imbeciles from the Oval Office?']
[[9, 10, 11, 12, 13, 14, 15], 'wow this lunatic kid we have as pm is now trying to suck in the world to his lame useless apologies!']
[[10, 11,

...

[[818, 819, 820, 821, 822, 823, 824, 825, 826, 836, 837, 838, 839], 'atilter>  Very good points that you address in your post.  It is the ulterior motive of the DEMs/LIBs to somehow "disarm" the American people.  Do away with the 2d Amendment,  and the right to bear arms.  There was a very strong reason why the founding fathers of this nation put that provision in the Constitution.  The "Socialist" or "commies" want to weaken the people\'s ability to fight any tyranny or dictatorship from taking over our country.  Be wary of those who profess a hatred of guns, whatever their reason(s) may be!!!!  What needs to happen is that the right to carry concealed is made available to all law-abiding citizens after a vetting process.  This will help to bring down crime for sure.  The argument presented by the DEMs/LIBs will hurt the law-abiding citizens and make the crooks, thieves and murderers happy.  Such sad people in our society, we need to have our country drained of these delusional people

[[124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135], 'A perfect post ... accurate, succinct and (best of all) it ends/closes with a reasonable proposal to deal with this obvious cluster-fuck.']
[[8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21], 'but you ignorant loser the libs ARE going to be funding this with our taxes!!!']
[[6, 7, 8, 9, 10, 11, 12], 'Utter rubbish.\nProvide a credible link to support your nonsense....']
[[145, 146, 147, 148], 'They will have a hard time explaining how they needed to shoot 17 bullets at somebody running away from them and throwing rocks. What a bunch of crap!']
[[167, 168, 169, 170, 171, 172, 173, 174, 175], 'Yes, businesses (and people, businesses being people, right?) should be able to pollute all they want, not hire blacks, pay women less, and hire 12 year olds to be be strippers.']
[[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 

[[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159], 'Sorry Bob, but the reason we have a vapid, ignorant boor like Trump for President is because 1) The other major party offered up an arrogant, deceitful liar and 2) Because the unelected leadership of both major parties have done an excellent job of convincing the public that they MUST choose between the t

[[435, 436, 437, 438, 439, 440, 441, 442, 443], 'yet its the left that are the lunatic fringe period with no care to economic sanity, finances , debt or reality, LIKE YOU!,, teh tea party is the most sane group of them all, if you had a clue what they were about you would agree,, see ignorant one they are about paying taxes but NO MORE< they pay enough thus its time for government to stop the spending insanity.. maybe you and that nut job rmiller should get a room and share your stupidity together']
[[46, 47, 48, 49, 50], 'What is wrong with you? Get your own account, troll.']
[[0, 1, 2, 3, 4, 5], "Stupid Politics is stupid no matter what side is doing it. Red or green, in the end, all that bringing up irrelevant political discussion does is further polarizes society, which makes more people think _this_ is the right idea. \n\nIt's not. Hodgkinson has done more damage to his cause than any politician has ever done to it. He's a fool. His choice to break out a firearm and attack the Rep

[[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11], "Kill 'em all!  They don't belong there.  /s"]
[[33, 34, 35, 36, 37, 38, 39, 40], 'I can only shake my head at this ignorant, racist excuse for a human being.  She is a disgrace to every living thing.']
[[4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24], 'The Liberals are traitors. Period.']
[[123, 124, 125, 126], '... we should move all our pollution creating entities to downtown Cheyenne so that those that LOVE all that pollution can SUCK ON IT ...']
[[9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 52, 53, 54, 55, 56, 57, 58, 59, 60, 62, 63, 64, 65], 'Trump is delusional, psychiatrically unsound, and a psychotic liar. No one should trust him.']
[[73, 74, 75, 76, 77, 78], 'wow posting blogs as some fact sources is really the left desperation of stupid']
[[198, 199, 200, 201, 202, 203, 204, 205, 206], 'Other states may have taxes, but they have less corruption than Alaska so the taxes are put to a better use.  In Alaska, tax

In [29]:
spans = []
sentences = []
for i in range(len(df)):
    spans += [df[i][0]]
    sentences += [df[i][1]]

In [30]:
print(spans)

[[8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39], [33, 34, 35, 36, 37, 38, 39], [0, 1, 2, 3], [7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17], [32, 33, 34, 35, 36, 37, 38], [], [39, 40, 41, 42, 43, 44, 46, 47, 48, 49, 50, 51, 52, 53, 54], [0, 1, 2, 3], [49, 50, 51, 52, 53, 54, 147, 148, 149, 150, 151, 152], [32, 33, 34, 35, 36, 37, 38, 39], [223, 224, 225, 226, 227, 228, 229, 230], [187, 188, 189, 190, 191], [78, 79, 80, 81, 82, 83, 84, 85, 86], [38, 39, 40, 41], [193, 194, 195, 196, 197, 198, 199], [164, 165, 166, 167, 168, 169, 170, 171], [87, 88, 89, 90, 91, 92], [7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 23, 24, 25, 26, 27, 28, 29, 30, 31], [86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 199, 200, 201], [12, 13, 14, 15], [0, 1, 2, 3, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71], [], [99, 100, 101, 102], [217, 218, 219, 220, 221, 222, 223, 224], [], [0, 1, 2, 3], [574, 575, 57

In [31]:
print(sentences)

['Another violent and aggressive immigrant killing a innocent and intelligent US Citizen.... Sarcasm', 'I am 56 years old, I am not your fucking junior pal. What you are saying makes no sense. I don\'t know what you are basing this on. The cheap black market crap is still coming up from Mexican nationals, and the good stuff from BC and Humbolt.  The I5 corridor is still just as busy, and they are still making a ton of money. Nothing has really changed except that the legal market has made it easy for anyone of legal age to buy it.  And the legal market is controlled by corporate growers with million dollar facilities, or a co-op of smaller growers. The Federal government "war on drugs" really has no impact on the legal market in Oregon. I don\'t see any glutton of weed, whatever that means.', 'Damn, a whole family. Sad indeed.', 'What a knucklehead. How can anyone not know this would be offensive??', '"who do you think should do the killing?"\n\nAnyone and everyone. This is a community

In [32]:
import re

class Preprocessor:
    def __init__(self, punctuation=True, url=True, number=True):
        self.punctuation = punctuation
        self.url = url
        self.number = number

    def apply(self, sentence: str) -> str:
        """ Apply the preprocessing rules to the sentence
        Args:
            sentence: raw sentence
        Returns:
            sentence: clean sentence
        """
        sentence = sentence.lower()
        if self.url:
            sentence = Preprocessor.remove_url(sentence)
        if self.punctuation:
            sentence = Preprocessor.remove_punctuation(sentence)
        if self.number:
            sentence = Preprocessor.remove_number(sentence)
        sentence = re.sub(r'\s+', ' ', sentence)
        return sentence

    @staticmethod
    def remove_punctuation(sentence: str) -> str:
        """ Remove punctuations in sentence with re
        Args:
            sentence: sentence with possible punctuations
        Returns:
            sentence: sentence without punctuations
        """
        # Start your code here
        sentence = re.sub(r'[^\w\s]', '',sentence)
        # End
        return sentence
    
    @staticmethod
    def remove_url(sentence: str) -> str:
        """ Remove urls in text with re
        Args:
            sentence: sentence with possible urls
        Returns:
            sentence: sentence without urls
        """
        # Start your code here
        sentence = re.sub(r'http\S+', '', sentence)
        # End
        return sentence

    @staticmethod
    def remove_number(sentence: str) -> str:
        """ Remove numbers in sentence with re
        Args:
            sentence: sentence with possible numbers
        Returns:
            sentence: sentence without numbers
        """
        # Start your code here
        sentence = re.sub(r'[0-9]+', '', sentence)
        # End
        return sentence

In [33]:
processor = Preprocessor()
clean_sentences = []
for i in range(len(df)):
    clean_sentences += [processor.apply(sentences[i])]

In [34]:
print(clean_sentences)

['another violent and aggressive immigrant killing a innocent and intelligent us citizen sarcasm', 'i am years old i am not your fucking junior pal what you are saying makes no sense i dont know what you are basing this on the cheap black market crap is still coming up from mexican nationals and the good stuff from bc and humbolt the i corridor is still just as busy and they are still making a ton of money nothing has really changed except that the legal market has made it easy for anyone of legal age to buy it and the legal market is controlled by corporate growers with million dollar facilities or a coop of smaller growers the federal government war on drugs really has no impact on the legal market in oregon i dont see any glutton of weed whatever that means', 'damn a whole family sad indeed', 'what a knucklehead how can anyone not know this would be offensive', 'who do you think should do the killing anyone and everyone this is a community problem so everyone who wants to be part of

In [35]:
dataframe

spans  \
0     [8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19,...   
1                          [33, 34, 35, 36, 37, 38, 39]   
2                                          [0, 1, 2, 3]   
3             [7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17]   
4                          [32, 33, 34, 35, 36, 37, 38]   
...                                                 ...   
7934                                     [8, 9, 10, 11]   
7935  [48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 5...   
7936  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13,...   
7937                            [5, 6, 7, 8, 9, 10, 11]   
7938  [106, 107, 108, 109, 110, 169, 170, 171, 172, ...   

                                                   text  
0     Another violent and aggressive immigrant killi...  
1     I am 56 years old, I am not your fucking junio...  
2                     Damn, a whole family. Sad indeed.  
3     What a knucklehead. How can anyone not know th...  
4     "who do you think should do the killing?"\n\nA...  
...                                                 ...  
7934                             Another fool pipes in.  
7935  So if a restaurant owner puts up a sign saying...  
7936  Any faith that can't stand up to logic and rea...  
7937  This idiotic. Use the surplus to pay down the ...  
7938  Who is this "we" of which you speak? Are you r...  

[7939 rows x 2 columns]

In [36]:
test_set = pd.read_csv("/home/harsh/Downloads/tsd_test.csv")
test_set['spans'] = test_set['spans'].apply(lambda x : json.loads(x))
train_set = pd.read_csv("/home/harsh/Downloads/tsd_train.csv")
train_set['spans'] = train_set['spans'].apply(lambda x : json.loads(x))
toxic_span_dataset = test_set.append(train_set,ignore_index=True)
toxic_span_dataset['text'] = toxic_span_dataset['text'].apply(lambda x : x.lower())

/tmp/ipykernel_17813/812741752.py:5: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  toxic_span_dataset = test_set.append(train_set,ignore_index=True)


In [37]:
def createNEROutputs(texts,spans,max_length,tokenizer):
    outputs = []
    for text,span in zip(texts,spans):
        output = np.zeros(max_length*3,dtype=np.float).reshape((max_length,3))
        tokens = tokenizer.tokenize(text)[:max_length]
        length = 0
        start = True
        for i in range(len(tokens),max_length):
            output[i,0] = 1.0
        for index,token in enumerate(tokens):
            sub = True
            if "Ġ" in token:
                sub = False
                token = token[1:]
            if not start:
                next_index = text[length:].find(token)
                if next_index == 0:
                    sub = True
                length += next_index
            # if length in span and not sub:
            #     output[index,2] = 1.0
            #     output[index,0] = 0.0
            if length in span:
                output[index,2] = 1.0
                output[index,0] = 0.0
            else:
                output[index,1] = 1.0
                output[index,0] = 0.0
            length += len(token)
            start = False
        outputs.append(output)
    return np.array(outputs)

In [38]:
def NERGetIndicesSingleText(outputs,text,tokenizer):
    outputs = tf.argmax(outputs,axis=-1)
    tokens = tokenizer.tokenize(text)
    index = 0
    indexes = []
    sub = False
    prev = False
    for token,output in zip(tokens,outputs):
        if token[0] == "Ġ":
            token = token[1:]
            sub = False
        elif token.isalpha():
            sub = True
        else:
            sub = False
        temp_index = text[index:].find(token)
        temp_start = index+temp_index
        if output == 2 or (sub and prev and output != 0):
            prev = True
            indexes = indexes + list(range(temp_start,temp_start+len(token)))
        else:
            prev = False
        index = temp_start+len(token)
    return np.array(indexes)

In [39]:
def createIndicesForNERModel(predicts,texts,tokenizer):
    outputs = []
    for text,pred in zip(texts,predicts):
         indices = NERGetIndicesSingleText(pred,text,tokenizer)
         outputs.append(indices)
    return outputs

In [40]:
def f1(preds,trues):
    if len(trues) == 0:
        return 1. if len(preds) == 0 else 0.
    if len(preds) == 0:
        return 0.
    predictions_set = set(preds)
    gold_set = set(trues)
    nom = 2 * len(predictions_set.intersection(gold_set))
    denom = len(predictions_set) + len(gold_set)
    return float(nom)/float(denom)

In [41]:
def avg_f1(preds,trues):
    avg_f1_total = 0.0
    for pred,true in zip(preds,trues):
        avg_f1_total += f1(pred,true)
    return avg_f1_total/len(preds)

In [42]:
class F1Metric(callbacks.Callback):
    def __init__(self,inputs,labels,spans,texts,test=True):
        self.inputs = inputs
        self.spans = spans
        self.tokenizer = tokenizer
        self.texts = texts
        self.test = test

    def on_epoch_end(self, epoch, logs={}):
        preds = self.model.predict(self.inputs,verbose=0)
        indices = createIndicesForNERModel(preds,texts,tokenizer)
        f1 = avg_f1(indices,self.spans)
        if self.test:
            print()
            print("test f1 = "+str(f1))
        else:
            print()
            print("train f1 = "+str(f1))

In [43]:
def createInputForNER(texts,max_length,tokenizer):
    input_length = []
    for text in texts:
        input_length.append(min(max_length,len(tokenizer.tokenize(text))))
    tokens = tokenizer(texts,padding="max_length",max_length=max_length,return_tensors="tf",truncation=True)
    data = [np.array(tokens['input_ids']),np.array(tokens['attention_mask']),np.array(input_length)]
    return data

In [44]:
try:
    from tensorflow.contrib.crf import crf_decode
except ImportError:
    from tensorflow.python.framework import dtypes
    from tensorflow.python.ops import array_ops, gen_array_ops, math_ops, rnn, rnn_cell

In [45]:
class CrfDecodeForwardRnnCell(rnn_cell.RNNCell):
    def __init__(self, transition_params):
        self._transition_params = array_ops.expand_dims(transition_params, 0)
        self._num_tags = transition_params.get_shape()[0]

    @property
    def state_size(self):
        return self._num_tags

    @property
    def output_size(self):
        return self._num_tags

    def __call__(self, inputs, state, scope=None):
        state = array_ops.expand_dims(state, 2)  # [B, O, 1]
        transition_scores = state + self._transition_params  # [B, O, O]
        new_state = inputs + math_ops.reduce_max(transition_scores, [1])  # [B, O]
        backpointers = math_ops.argmax(transition_scores, 1)
        backpointers = math_ops.cast(backpointers, dtype=dtypes.int32)  # [B, O]
        return backpointers, new_state

In [46]:
class CrfDecodeBackwardRnnCell(rnn_cell.RNNCell):
    def __init__(self, num_tags):
        self._num_tags = num_tags

    @property
    def state_size(self):
        return 1

    @property
    def output_size(self):
        return 1

    def __call__(self, inputs, state, scope=None):
        state = array_ops.squeeze(state, axis=[1])  # [B]
        batch_size = array_ops.shape(inputs)[0]
        b_indices = math_ops.range(batch_size)  # [B]
        indices = array_ops.stack([b_indices, state], axis=1)  # [B, 2]
        new_tags = array_ops.expand_dims(
            gen_array_ops.gather_nd(inputs, indices),  # [B]
            axis=-1)  # [B, 1]

        return new_tags, new_tags

In [47]:
def crf_decode(potentials, transition_params, sequence_length):
    num_tags = potentials.get_shape()[2]

    # Computes forward decoding. Get last score and backpointers.
    crf_fwd_cell = CrfDecodeForwardRnnCell(transition_params)
    initial_state = array_ops.slice(potentials, [0, 0, 0], [-1, 1, -1])
    initial_state = array_ops.squeeze(initial_state, axis=[1])  # [B, O]
    inputs = array_ops.slice(potentials, [0, 1, 0], [-1, -1, -1])  # [B, T-1, O]
    backpointers, last_score = rnn.dynamic_rnn(
        crf_fwd_cell,
        inputs=inputs,
        sequence_length=sequence_length - 1,
        initial_state=initial_state,
        time_major=False,
        dtype=dtypes.int32)  # [B, T - 1, O], [B, O]
    backpointers = gen_array_ops.reverse_sequence(backpointers, sequence_length - 1, seq_dim=1)  # [B, T-1, O]

    # Computes backward decoding. Extract tag indices from backpointers.
    crf_bwd_cell = CrfDecodeBackwardRnnCell(num_tags)
    initial_state = math_ops.cast(math_ops.argmax(last_score, axis=1), dtype=dtypes.int32)  # [B]
    initial_state = array_ops.expand_dims(initial_state, axis=-1)  # [B, 1]
    decode_tags, _ = rnn.dynamic_rnn(
        crf_bwd_cell,
        inputs=backpointers,
        sequence_length=sequence_length - 1,
        initial_state=initial_state,
        time_major=False,
        dtype=dtypes.int32)  # [B, T - 1, 1]
    decode_tags = array_ops.squeeze(decode_tags, axis=[2])  # [B, T - 1]
    decode_tags = array_ops.concat([initial_state, decode_tags], axis=1)  # [B, T]
    decode_tags = gen_array_ops.reverse_sequence(decode_tags, sequence_length, seq_dim=1)  # [B, T]

    best_score = math_ops.reduce_max(last_score, axis=1)  # [B]
    return decode_tags, best_score

In [48]:
class CRFLayer(Layer):

    def __init__(self, transition_params=None, **kwargs):
        super(CRFLayer, self).__init__(**kwargs)
        self.transition_params = transition_params
        self.input_spec = [InputSpec(ndim=3), InputSpec(ndim=2)]
        self.supports_masking = True

    def compute_output_shape(self, input_shape):
        assert input_shape and len(input_shape[0]) == 3

        return input_shape[0]

    def build(self, input_shape):
        assert len(input_shape) == 2
        assert len(input_shape[0]) == 3
        assert len(input_shape[1]) == 2
        n_steps = input_shape[0][1]
        n_classes = input_shape[0][2]
        assert n_steps is None or n_steps >= 2

        self.transition_params = self.add_weight(shape=(n_classes, n_classes),
                                                 initializer='uniform',
                                                 name='transition')
        self.input_spec = [InputSpec(dtype=backend.floatx(), shape=(None, n_steps, n_classes)),
                           InputSpec(dtype='int32', shape=(None, 1))]
        self.built = True

    def viterbi_decode(self, potentials, sequence_length):
        decode_tags, best_score = crf_decode(potentials, self.transition_params, sequence_length)
        return decode_tags

    def call(self, inputs, mask=None, **kwargs):
        inputs, sequence_lengths = inputs
        self.sequence_lengths = backend.flatten(sequence_lengths)
        y_pred = self.viterbi_decode(inputs, self.sequence_lengths)
        nb_classes = self.input_spec[0].shape[2]
        y_pred_one_hot = backend.one_hot(y_pred, nb_classes)

        return backend.in_train_phase(inputs, y_pred_one_hot)

    def loss(self, y_true, y_pred):
        y_true = backend.cast(backend.argmax(y_true, axis=-1), dtype='int32')
        log_likelihood, self.transition_params = tfa.text.crf.crf_log_likelihood(
            y_pred, y_true, self.sequence_lengths, self.transition_params)
        loss = tf.reduce_mean(-log_likelihood)

        return loss

    def get_config(self):
        config = {
            'transition_params': backend.eval(self.transition_params),
        }
        base_config = super(CRFLayer, self).get_config()

        return dict(list(base_config.items()) + list(config.items()))

In [49]:
def create_custom_objects():
    instanceHolder = {'instance': None}

    class ClassWrapper(CRFLayer):
        def __init__(self, *args, **kwargs):
            instanceHolder['instance'] = self
            super(ClassWrapper, self).__init__(*args, **kwargs)

    def loss(*args):
        method = getattr(instanceHolder['instance'], 'loss')
        return method(*args)

    return {'CRFLayer': ClassWrapper, 'loss': loss}

In [50]:
tokenizer = RobertaTokenizer.from_pretrained('roberta-base')
# base_model = TFBertModel.from_pretrained('bert-base-uncased')

In [51]:
def createToxicModelWithGivenBaseModel(max_input_length,base_model):
    input_ids_layer = layers.Input(shape=(max_input_length,),name="encoder_input_ids",dtype=tf.int32)
    input_attention_mask_layer = layers.Input(shape=(max_input_length,),name="encoder_attention_mask",dtype=tf.int32)
    input_length = layers.Input(shape=(1,),name="length",dtype=tf.int32)
    base_model.trainable = True
    base_model = base_model(input_ids_layer,attention_mask=input_attention_mask_layer,return_dict=True)
    output = layers.Dropout(0.1)(base_model.last_hidden_state)
    output = layers.Dense(1024,activation="relu")(output)
    output = layers.Dropout(0.1)(output)
    output = layers.Dense(1024,activation="relu")(output)
    output = layers.Dense(3,activation="linear")(output)
    crf = CRFLayer()
    output = crf(inputs=[output,input_length])
    model = models.Model(inputs=[input_ids_layer,input_attention_mask_layer,input_length],outputs=output)
    model.compile(optimizer=optimizers.Adam(learning_rate=3e-5),loss=crf.loss,metrics=['accuracy'])
    return model

In [52]:
max_length = 400

In [53]:
texts = toxic_span_dataset['text'].to_numpy()
targets = createNEROutputs(texts,toxic_span_dataset['spans'],max_length,tokenizer)
all_spans = toxic_span_dataset['spans'].to_numpy()
result_test = []
result_train = []
kf = KFold(n_splits=5)
train_test_indices = []
for train_index,test_index in kf.split(texts):
    train_test_indices.append((train_index,test_index))

In [54]:
train_index,test_index = train_test_indices.pop()
x_train , x_test = list(texts[train_index]) , list(texts[test_index])
y_train , y_test = targets[train_index] , targets[test_index]
model = None
base_model = None
gc.collect()
tf.keras.backend.clear_session()
base_model = TFRobertaModel.from_pretrained('roberta-base')
model = createToxicModelWithGivenBaseModel(max_length,base_model)
train_data = createInputForNER(x_train,max_length,tokenizer)
test_data = createInputForNER(x_test,max_length,tokenizer)
spans_test = all_spans[test_index]
spans_train = all_spans[train_index]
model.fit(train_data,y_train,batch_size=16,epochs=2)
preds = model.predict(test_data)
indices = createIndicesForNERModel(preds,x_test,tokenizer)
f1_toxic = avg_f1(indices,spans_test)
print("test F1 = %f"%(f1_toxic))
result_test.append(f1_toxic)
preds = model.predict(train_data)
indices = createIndicesForNERModel(preds,x_train,tokenizer)
f1_toxic = avg_f1(indices,spans_train)
print("train F1 = %f"%(f1_toxic))
result_train.append(f1_toxic)

2022-12-21 15:45:51.116832: I tensorflow/core/platform/cpu_feature_guard.cc:142] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
Some layers from the model checkpoint at roberta-base were not used when initializing TFRobertaModel: ['lm_head']
- This IS expected if you are initializing TFRobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFRobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFRobertaModel were initialized from the model checkpoint at ro

Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: '<' not supported between instances of 'str' and 'Literal'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: '<' not supported between instances of 'str' and 'Literal'
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Instructions for updating:
The `validate_indices` argument has no effect. Indices are always validated on CPU and never validated on GPU.
Instructions for updating:
Please use `keras.layers.RNN(cell)`, which is equivalent to this API


/tmp/tmpczsve7ob.py:125: SyntaxWarning: "is" with a literal. Did you mean "=="?
  ag__.if_stmt(ag__.or_(lambda : ag__.ld(training) is 0, lambda : ag__.ld(training) is False), if_body_3, else_body_3, get_state_3, set_state_3, ('do_return', 'retval_'), 2)
/tmp/tmpczsve7ob.py:161: SyntaxWarning: "is" with a literal. Did you mean "=="?
  ag__.if_stmt(ag__.or_(lambda : ag__.ld(training) is 1, lambda : ag__.ld(training) is True), if_body_6, else_body_6, get_state_6, set_state_6, ('do_return', 'retval_', 'x._uses_learning_phase', 'x'), 3)


AttributeError: in user code:

    /tmp/ipykernel_17813/3114152609.py:40 call  *
        return backend.in_train_phase(inputs, y_pred_one_hot)
    /home/harsh/anaconda3/lib/python3.9/site-packages/keras/backend/tensorflow_backend.py:3105 in_train_phase  *
        training = learning_phase()
    /home/harsh/anaconda3/lib/python3.9/site-packages/keras/backend/tensorflow_backend.py:131 learning_phase  *
        graph = tf.get_default_graph()

    AttributeError: module 'tensorflow' has no attribute 'get_default_graph'
